# T2D benchmark

In [1]:
%matplotlib inline
%load_ext autoreload
%autoreload 2
import os
os.chdir('../../')

In [2]:
import takco
conf = takco.Config('resources/config-dbpedia.toml')
t2dv2 = takco.TableSet.dataset('t2d-v2', **conf)

takco.preview(t2dv2)

In [43]:
%%time
import takco.link

kbs = {k.get("name", k.get("class")): takco.Config(k) for k in conf['kbs']}
# searcher_config = takco.Config({'name': 'dbpedialookup_t2ksubset'}, **kbs)
searcher_config = takco.Config({'name': 'dbpedia_t2ksubset_extralabels'}, **kbs)
searcher_config = takco.Config({
    'name': 'es',
    'class': 'ElasticSearcher',
    'index': 'test-1',
    'baseuri': 'http://dbpedia.org/resource/',
})

pred = takco.TableSet.link(
    takco.HashBag(list(t2dv2)[:5]),
    usecols = "keycol",
    lookup_config = None,
    linker_config = takco.Config({
        "class": "First",
        "limit": 50,
        "search_limit": 50,
        "searcher": searcher_config,
#         "majority_class": "http://www.w3.org/1999/02/22-rdf-syntax-ns#type",
    }),
)
scored = takco.TableSet.score(pred, labels='t2d-v2', **conf)

report = takco.TableSet.report( scored, keycol_only=True )
report

CPU times: user 2.82 s, sys: 359 ms, total: 3.17 s
Wall time: 21.5 s


{'scores': {'entities': {'precision': 0.1237785016286645,
   'recall': 0.8988173455978975,
   'f1-score': 0.21759185621122953,
   'support': 761,
   'predictions': 5526}}}

In [36]:
takco.preview( scored, nrows=None, hide_correct_rows=True )

In [10]:
!time takco run -v -C resources/config-dbpedia.toml resources/pipelines/t2d-v2-baseline.toml

INFO:root:Set log level to 20
INFO:root:Loaded config {'name': 'config-dbpedia', 'datadir': 'data', 'resourcedir': 'resources', 'cache': False, 'kbs': [{'name': 'dbpedia_t2ksubset', 'class': 'RDFSearcher', 'labelProperties': ['http://dbpedia.org/ontology/title'], 'store': {'class': 'Trident', 'configuration': 'kb/dbpedia_t2ksubset/db/'}}, {'name': 'dbpedia_2014_part2', 'class': 'RDFSearcher', 'labelProperties': ['http://dbpedia.org/ontology/title'], 'store': {'class': 'Trident', 'configuration': 'kb/dbpedia/2014_part2/'}}, {'name': 'dbpedia_2016', 'class': 'RDFSearcher', 'labelProperties': ['http://dbpedia.org/ontology/title'], 'store': {'class': 'Trident', 'configuration': 'kb/dbpedia/2016-10/'}}, {'name': 'dbpedialookup', 'class': 'DBpediaLookup'}], 'assets': [{'name': 't2d-v1', 'class': 'T2D', 'download': ['http://webdatacommons.org/webtables/tables_instance.tar.gz', 'http://webdatacommons.org/webtables/entities_instance.tar.gz', 'http://webdatacommons.org/webtables/classes_instance